Install dependencies

In [ ]:
pip install polyline

In [ ]:
pip install geopy

Import

In [ ]:
from geopy.geocoders import Nominatim
import numpy as np
from numpy import arange
import pickle
import requests
import folium
import polyline
import json
from queue import PriorityQueue
from google.colab import files

Test geolocator

In [ ]:
geolocator = Nominatim(user_agent="http")
location = geolocator.geocode("bits pilani")
print(location.address)
print(location.raw)

bits pilani, Lover's Lane, Kapra mandal, Medchal–Malkajgiri, Telangana, 500087, India
{'place_id': 51375158, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright', 'osm_type': 'node', 'osm_id': 4293343216, 'boundingbox': ['17.547181', '17.547281', '78.5725123', '78.5726123'], 'lat': '17.547231', 'lon': '78.5725623', 'display_name': "bits pilani, Lover's Lane, Kapra mandal, Medchal–Malkajgiri, Telangana, 500087, India", 'class': 'highway', 'type': 'bus_stop', 'importance': 0.201, 'icon': 'https://nominatim.openstreetmap.org/ui/mapicons//transport_bus_stop2.p.20.png'}


Get all locations

In [ ]:
results = []

min_lat = 17.1933
max_lat = 17.6139
min_long = 78.2185
max_long = 78.7033


for cur_lat in arange(min_lat, max_lat, 0.05):

  for cur_long in arange(min_long, max_long, 0.05):

    query = str(cur_lat) + ", " + str(cur_long)
    #print(query)

    location = geolocator.reverse(query)

    if location.raw['osm_type'] == 'way':
      if location not in results:
        results.append(location)
    

all_loc = dict()

for l in results:

  if l.raw['display_name'] not in all_loc:
    all_loc.update({l.raw['display_name']:{'latitude':l.latitude, 'longitude':l.longitude}})


for l, ad in all_loc.items():
  print((l, ad))

print(len(all_loc))

('Akkaivaniguda, Gudur, Kothur mandal, Rangareddy, Telangana, 50128, India', {'latitude': 17.1934719, 'longitude': 78.2739932})
('Patha Tanda, Shamshabad mandal, Rangareddy, Telangana, India', {'latitude': 17.193569822460628, 'longitude': 78.3189424968233})
('Maheswaram mandal, Rangareddy, Telangana, 500006, India', {'latitude': 17.192852079101296, 'longitude': 78.4183954480796})
('Mankhal, Maheswaram mandal, Rangareddy, Telangana, 501359, India', {'latitude': 17.1929973802187, 'longitude': 78.46757291261527})
('Ibrahimpatnam mandal, Rangareddy, Telangana, India', {'latitude': 17.194276, 'longitude': 78.5195447})
('Uppariguda, Ibrahimpatnam mandal, Rangareddy, Telangana, 501506, India', {'latitude': 17.1905486, 'longitude': 78.6152101})
('Raipole, Rain Guda, Raipole, Ibrahimpatnam mandal, Rangareddy, Telangana, 501506, India', {'latitude': 17.19264800167316, 'longitude': 78.66846915680478})
('Rudraram, Shabad mandal, Rangareddy, Telangana, 50128, India', {'latitude': 17.2484821, 'longi

pickle locations

In [ ]:
def storeData():

  my_nodes = open('node_pickle_osm_dict_05', 'ab')
  files.download('node_pickle_osm_dict_05')
  pickle.dump(all_loc, my_nodes)
  my_nodes.close()

def loadData():

  my_nodes = open('node_pickle_osm_dict_05', 'rb')

  resul = pickle.load(my_nodes)
  my_nodes.close()

  return resul

In [ ]:
storeData()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
all_loc = loadData()

In [ ]:
origin = geolocator.geocode("RGIA Airport Hyderabad")
#print(origin.raw)
all_loc.update({origin.raw['display_name']:{'latitude':origin.latitude, 'longitude':origin.longitude}})
destination = geolocator.geocode("bits pilani")
#print(destination.raw)
all_loc.update({destination.raw['display_name']:{'latitude':destination.latitude, 'longitude':destination.longitude}})

Make Network

In [ ]:
def getRoute(pickup_lon, pickup_lat, dropoff_lon, dropoff_lat):
    
    loc = "{},{};{},{}".format(pickup_lon, pickup_lat, dropoff_lon, dropoff_lat)
    url = "http://router.project-osrm.org/route/v1/driving/"
    r = requests.get(url + loc) 
    if r.status_code!= 200:
      print('No route')
      return {}
  
    res = r.json()   
    routes = polyline.decode(res['routes'][0]['geometry'])
    start_point = [res['waypoints'][0]['location'][1], res['waypoints'][0]['location'][0]]
    end_point = [res['waypoints'][1]['location'][1], res['waypoints'][1]['location'][0]]
    distance = res['routes'][0]['distance']
    
    out = {'route':routes,
           'start_point':start_point,
           'end_point':end_point,
           'distance':distance
          }

    return out

In [ ]:
all_routes = dict()

boundto = 0.15

for start in all_loc:
  for end in all_loc:

    if all_loc[end]['latitude'] < all_loc[start]['latitude']+boundto and all_loc[end]['latitude'] > all_loc[start]['latitude']-boundto and all_loc[end]['longitude'] < all_loc[start]['longitude']+boundto and all_loc[end]['longitude'] > all_loc[start]['longitude']-boundto:
      if start != end:
      #all_routes[start][end] = getRoute(all_loc[start]['longitude'], all_loc[start]['latitude'], all_loc[end]['longitude'], all_loc[end]['latitude'])
        if start not in all_routes:
          all_routes.update({start:{end:getRoute(all_loc[start]['longitude'], all_loc[start]['latitude'], all_loc[end]['longitude'], all_loc[end]['latitude'])}})
        else:
          all_routes[start].update({end:getRoute(all_loc[start]['longitude'], all_loc[start]['latitude'], all_loc[end]['longitude'], all_loc[end]['latitude'])})
        all_routes[start][end]['distance'] = int(all_routes[start][end]['distance'])
        print((start, end))


('Akkaivaniguda, Gudur, Kothur mandal, Rangareddy, Telangana, 50128, India', 'Patha Tanda, Shamshabad mandal, Rangareddy, Telangana, India')
('Akkaivaniguda, Gudur, Kothur mandal, Rangareddy, Telangana, 50128, India', 'Maheswaram mandal, Rangareddy, Telangana, 500006, India')
('Akkaivaniguda, Gudur, Kothur mandal, Rangareddy, Telangana, 50128, India', 'Rudraram, Shabad mandal, Rangareddy, Telangana, 50128, India')
('Akkaivaniguda, Gudur, Kothur mandal, Rangareddy, Telangana, 50128, India', 'NH44, Gandiguda, Shamshabad mandal, Rangareddy, Telangana, 501218, India')
('Akkaivaniguda, Gudur, Kothur mandal, Rangareddy, Telangana, 50128, India', 'Velankanni Nagar, Shamshabad, Shamshabad mandal, Rangareddy, Telangana, 509218, India')
('Akkaivaniguda, Gudur, Kothur mandal, Rangareddy, Telangana, 50128, India', 'Surangal, Moinabad mandal, Rangareddy, Telangana, 501504, India')
('Akkaivaniguda, Gudur, Kothur mandal, Rangareddy, Telangana, 50128, India', 'Nagireddyguda, Moinabad mandal, Rangaredd

In [ ]:
print(len(all_routes))

80


pickle all routes

In [ ]:
def storeDataRoute():

  my_nodes = open('route_pickle_osm_dict_05', 'ab')
  files.download('route_pickle_osm_dict_05')
  pickle.dump(all_routes, my_nodes)
  my_nodes.close()

def loadDataRoute():

  my_nodes = open('route_pickle_osm_dict_05', 'rb')

  resul = pickle.load(my_nodes)
  my_nodes.close()

  return resul

In [ ]:
storeDataRoute()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
all_routes = loadDataRoute()

Get heuristics

In [ ]:
from geopy.distance import geodesic
  
h = list()

for loc in all_loc:
  h.append(int(geodesic((all_loc[loc]['latitude'], all_loc[loc]['longitude']), (all_loc["bits pilani, Lover's Lane, Kapra mandal, Medchal–Malkajgiri, Telangana, 500087, India"]['latitude'], all_loc["bits pilani, Lover's Lane, Kapra mandal, Medchal–Malkajgiri, Telangana, 500087, India"]['longitude'])).m))


A* Best First Search

In [ ]:
network = list()

In [ ]:
def addRoute(u, v, dist):

  network[u].append((v, dist))
  #network[v].append((u, dist))

In [ ]:
for x, y in all_routes.items():
  print((x,y))

('Akkaivaniguda, Gudur, Kothur mandal, Rangareddy, Telangana, 50128, India', {'Patha Tanda, Shamshabad mandal, Rangareddy, Telangana, India': {'route': [(17.19347, 78.27399), (17.19261, 78.27434), (17.19175, 78.27423), (17.18929, 78.27268), (17.18795, 78.27397), (17.18586, 78.27387), (17.18509, 78.27306), (17.1841, 78.27421), (17.18259, 78.27912), (17.18223, 78.28193), (17.18254, 78.28408), (17.18166, 78.28589), (17.18105, 78.2861), (17.17991, 78.28823), (17.1767, 78.2891), (17.17609, 78.28956), (17.1747, 78.28933), (17.17444, 78.2926), (17.17501, 78.29607), (17.17373, 78.30053), (17.18422, 78.30525), (17.18651, 78.30676), (17.19433, 78.31666), (17.19494, 78.31794), (17.19357, 78.31894)], 'start_point': [17.193472, 78.273993], 'end_point': [17.19357, 78.318942], 'distance': 8009}, 'Maheswaram mandal, Rangareddy, Telangana, 500006, India': {'route': [(17.19347, 78.27399), (17.19175, 78.27423), (17.18929, 78.27268), (17.18795, 78.27397), (17.18586, 78.27387), (17.18509, 78.27306), (17.18

In [ ]:

#locations = ['Arad', 'Zerind', 'Oradea', 'Sibiu', 'Fagaras', 'Bucharest', 'Pitesti', 'Rimnicu', 'Craiova', 'Drobeta', 'Mehadia', 'Lugoj', 'Timisoara']
locations = list()
for loc in all_loc:
  locations.append(loc)

#h = [366, 374, 380, 253, 176, 0, 100, 193, 160, 242, 241, 244, 329]
g = dict()
loc_to_i = dict()
ind = 0

for l in locations:
  loc_to_i[l] = ind
  ind+=1

network = [[] for i in range(len(locations))]

# addRoute(loc_to_i['Arad'], loc_to_i['Zerind'], 75)
# addRoute(loc_to_i['Oradea'], loc_to_i['Zerind'], 71)
# addRoute(loc_to_i['Oradea'], loc_to_i['Sibiu'], 151)
# addRoute(loc_to_i['Arad'], loc_to_i['Timisoara'], 118)
# addRoute(loc_to_i['Arad'], loc_to_i['Sibiu'], 140)
# addRoute(loc_to_i['Sibiu'], loc_to_i['Fagaras'], 99)
# addRoute(loc_to_i['Fagaras'], loc_to_i['Bucharest'], 211)
# addRoute(loc_to_i['Sibiu'], loc_to_i['Rimnicu'], 80)
# addRoute(loc_to_i['Rimnicu'], loc_to_i['Pitesti'], 97)
# addRoute(loc_to_i['Rimnicu'], loc_to_i['Craiova'], 146)
# addRoute(loc_to_i['Pitesti'], loc_to_i['Bucharest'], 101)
# addRoute(loc_to_i['Pitesti'], loc_to_i['Craiova'], 138)
# addRoute(loc_to_i['Craiova'], loc_to_i['Drobeta'], 120)
# addRoute(loc_to_i['Drobeta'], loc_to_i['Mehadia'], 75)
# addRoute(loc_to_i['Mehadia'], loc_to_i['Lugoj'], 70)
# addRoute(loc_to_i['Lugoj'], loc_to_i['Timisoara'], 111)

# for start in all_loc:
#   for end in all_loc:

#     if start != end:

#       addRoute(loc_to_i[start], loc_to_i[end], all_routes[start][end]['distance'])

for start in all_routes:
  for end in all_routes[start]:
    addRoute(loc_to_i[start], loc_to_i[end], all_routes[start][end]['distance'])

source = "Rajiv Gandhi International Airport, Airport Gokarting, Balapur mandal, Rangareddy, Telangana, India"
desti = "bits pilani, Lover's Lane, Kapra mandal, Medchal–Malkajgiri, Telangana, 500087, India"

src = loc_to_i[source]
dest = loc_to_i[desti]

previous = dict()

OPEN = PriorityQueue()
CLOSED = list()

OPEN.put((h[src], src))

p2_f = 0.1


draw map

In [ ]:
myMap = folium.Map(location=[(all_loc[source]['latitude'] + all_loc[desti]['latitude'])/2, (all_loc[source]['longitude'] + all_loc[desti]['longitude'])/2], zoom_start=11)

for loc in all_loc:
  
  folium.Marker(location=[all_loc[loc]['latitude'], all_loc[loc]['longitude']],tooltip=loc).add_to(myMap)

folium.Marker(location=[all_loc[source]['latitude'], all_loc[source]['longitude']],tooltip=source,icon = folium.Icon(icon='cloud', color='green')).add_to(myMap)
folium.Marker(location=[all_loc[desti]['latitude'], all_loc[desti]['longitude']],tooltip=desti,icon = folium.Icon(icon='home', color='green')).add_to(myMap)
myMap

In [ ]:
while OPEN.empty() == False:

  temp_pair = OPEN.get()
  city = temp_pair[1]
  curr_f = temp_pair[0]
  
  CLOSED.append(city)

  #print(locations[city])

  if city != src:
    print(f'from {locations[previous[city, curr_f]]} to {locations[city]} f(n)={curr_f}')
    curr_g = g[city, previous[city, curr_f]]

    folium.PolyLine(
        all_routes[locations[previous[city, curr_f]]][locations[city]]['route'],
        weight=8,
        color='blue',
        opacity=0.6,
         tooltip=all_routes[locations[previous[city, curr_f]]][locations[city]]['distance']
    ).add_to(myMap)

    folium.Marker(
        location=all_routes[locations[previous[city, curr_f]]][locations[city]]['start_point'],
        #icon=folium.Icon(icon='play', color='green'),
        tooltip = locations[previous[city, curr_f]]
    ).add_to(myMap)

    folium.Marker(
        location=all_routes[locations[previous[city, curr_f]]][locations[city]]['end_point'],
        #icon=folium.Icon(icon='stop', color='red'),
        tooltip = locations[city]
    ).add_to(myMap)

  else:
    curr_g = 0

  if city == dest:
    p2_f = curr_f
    print('REACHED')
    break

  for to, dis in network[city]:

    if to not in CLOSED:
      g_n = dis + curr_g
      f_n = g_n + h[to]

      g[to, city] = g_n
      previous[to, f_n] = city
      OPEN.put((f_n, to))

from Rajiv Gandhi International Airport, Airport Gokarting, Balapur mandal, Rangareddy, Telangana, India to Velankanni Nagar, Shamshabad, Shamshabad mandal, Rangareddy, Telangana, 509218, India f(n)=40078
from Rajiv Gandhi International Airport, Airport Gokarting, Balapur mandal, Rangareddy, Telangana, India to Mustafa Hills, Bandlaguda mandal, Hyderabad, Telangana, 500036, India f(n)=43209
from Rajiv Gandhi International Airport, Airport Gokarting, Balapur mandal, Rangareddy, Telangana, India to Jahanuma, Ward 54 Jahanuma, Hyderabad, Bahadurpura mandal, Hyderabad, Telangana, 500 064, India f(n)=44390
from Velankanni Nagar, Shamshabad, Shamshabad mandal, Rangareddy, Telangana, 509218, India to Gagan Pahad, Ward 59 Mailardevpally, Hyderabad, Rajendranagar mandal, Rangareddy, Telangana, 500030, India f(n)=44677
from Rajiv Gandhi International Airport, Airport Gokarting, Balapur mandal, Rangareddy, Telangana, India to Sikhara Colony, Ward 17 Champapet, Greater Hyderabad Municipal Corporat

In [ ]:
myMap

Final route

In [ ]:
p1 = 0
p2 = dest

while p2 != src:
  p1 = previous[p2, p2_f]
  
  #print(f'from {locations[p1]} to {locations[p2]} f(n)={p2_f}')

  folium.PolyLine(
      all_routes[locations[p1]][locations[p2]]['route'],
      weight=8,
      color='yellow',
      opacity=1,
      tooltip=all_routes[locations[p1]][locations[p2]]['distance']
  ).add_to(myMap)

  folium.Marker(
      location=all_routes[locations[p1]][locations[p2]]['start_point'],
      #icon=folium.Icon(icon='play', color='green'),
      tooltip=locations[p1]
  ).add_to(myMap)

  folium.Marker(
      location=all_routes[locations[p1]][locations[p2]]['end_point'],
      icon=folium.Icon(icon='stop', color='red'),
      tooltip=locations[p2]
  ).add_to(myMap)

  prev_g = g[p2, p1] - all_routes[locations[p1]][locations[p2]]['distance']
  prev_h = h[p1]

  #print(f'prev_g = {prev_g} prev_h = {prev_h}')

  p2_f = prev_g + prev_h
  p2 = p1

In [ ]:
myMap

In [ ]:
myMap.save("solved_05.html")
files.download("solved_05.html")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>